[View in Colaboratory](https://colab.research.google.com/github/Santosh-Gupta/BookCrossingsRecommender/blob/master/ChallengeProblemUpdated.ipynb)

Import Stuff, set connection to Google Drive

In [0]:
import pandas as pd

!pip install -U -q PyDrive

from google.colab import files
from pydrive.auth import GoogleAuth
from pydrive.drive import GoogleDrive
from google.colab import auth
from oauth2client.client import GoogleCredentials
import zipfile
import os
import sys

import random
import numpy as np
import pandas as pd

import re
from collections import Counter
import time


from __future__ import print_function
import collections
import math
import random
from six.moves import range
from six.moves.urllib.request import urlretrieve


from urllib.request import urlretrieve
from os.path import isfile, isdir
import tensorflow as tf
from matplotlib import pylab
from six.moves import range
from six.moves.urllib.request import urlretrieve
from sklearn.manifold import TSNE

!pip install -U -q PyDrive

from numpy import genfromtxt

auth.authenticate_user()
gauth = GoogleAuth()
gauth.credentials = GoogleCredentials.get_application_default()
drive = GoogleDrive(gauth)

Download BookCrossings data from Google Drive

In [5]:
dl_id = input("Enter Gdrive file ID for Book Crossings data file: ") # 1NIYYr2QZ9kSjavcpou08cYkyFJ83JpMh

# DOWNLOAD ZIP
print ("Downloading  file")
myzip = drive.CreateFile({'id': dl_id})
myzip.GetContentFile('data.csv')

print( os.listdir() )

Enter Gdrive file ID for Book Crossings data file: 1NIYYr2QZ9kSjavcpou08cYkyFJ83JpMh
['sample_data', '.config', 'adc.json', 'data.csv', 'ratings.csv']


Open data and convert to Pandas dataframe object. Look at number of rows (data points)

Columns must be renamed for Pandas compatability ( ie pd.Book-Rating will not work but pd.BookRating will)

I decided to filter out results where the rating was below a 6. Since these vectors are going to be used for book reccomendations, I decided to only train on data points where the books resulted in an enjoyable experience for the user.


In [6]:
with open('data.csv', 'rb') as f:
  text = f.read()
  
csvfile = pd.read_csv('data.csv',  encoding = "ISO-8859-1", error_bad_lines=False, delimiter=';')

csvfile.rename(columns={'Book-Rating': 'BookRating', 'User-ID': 'UserID'}, inplace=True)

csvfile6plus = csvfile[csvfile.BookRating >= 6] 
print(csvfile6plus.head())
csvfile6plus.shape[0] #check how many data points we have left

   UserID        ISBN  BookRating
4  276729  0521795028           6
6  276736  3257224281           8
7  276737  0600570967           6
8  276744  038550120X           7
9  276745   342310538          10


363268

Look at statics about the books. In the stats below, count is the total number of books and mean is the average amount of times a book appears in the data. Min is the occurance for the lowest occuring book, or multiple books if there are more than one book that has the same number for lowest occurance.

In [7]:
reviews_per_user45 = csvfile6plus.groupby( 'ISBN' ).UserID.apply( lambda x: len( x ))
reviews_per_user45.describe() 

count    159323.000000
mean          2.280073
std           6.418580
min           1.000000
25%           1.000000
50%           1.000000
75%           2.000000
max         663.000000
Name: UserID, dtype: float64

Filter out books that appear less than two times because books with lower instances will not get too many opportunities to train their embedding during each epoch. For example, a book that only occurs once in the data will only train once per epoch (assuming that each user appears at least twice in the data). Also, since these embeddings will be used for reccomendation, it would be ideal to have each book be reviewed by multiple users. But since I am not working with too much data, I decided to filter out books with only one occurance. 

In [0]:
over2users = csvfile6plus.groupby('ISBN').filter(lambda x: len(x) >= 2) 

Look at statics about the users. In the stats below, count is the total number of users and mean is the average amount of times a user appears in the data. Min is the occurance for the lowest occuring user, or multiple users if there are more than one user that has the same number for lowest occurance.

In [9]:
checkUsers = over2users.groupby( 'UserID' ).UserID.apply( lambda x: len( x ))
checkUsers.describe() 

count    56666.000000
mean         4.431846
std         28.388489
min          1.000000
25%          1.000000
50%          1.000000
75%          3.000000
max       5172.000000
Name: UserID, dtype: float64

It is necessary to have at least two occurances for each user. The word2vec-based algorithm will measure similiarity among all books rated by a user, and so there should be at least two books rated by a particular user. 

In [0]:
over2usersOver2books = csvfile6plus.groupby('UserID').filter(lambda x: len(x) >= 2) 

Check the stats of the books again, in case removing all instances of one user resulted in cases of only one book. 

Continue the cycle until there are at least 2 instances of each book and 2 instances of each user. 

In [0]:
checkBooks = over2usersOver2books.groupby( 'ISBN' ).ISBN.apply( lambda x: len( x )) 
over2usersOver2booksPart2 = over2usersOver2books.groupby('ISBN').filter(lambda x: len(x) >= 2)  #Since there are cases of only 1 user. 
checkBooks = over2usersOver2booksPart2.groupby( 'UserID' ).ISBN.apply( lambda x: len( x ))  #check to see if removing cases of 1 user created cases where there is only 1 book review
over2usersOver2booksPart3 = over2usersOver2booksPart2.groupby('UserID').filter(lambda x: len(x) >= 2) 
checkBooks = over2usersOver2booksPart3.groupby( 'ISBN' ).ISBN.apply( lambda x: len( x ))  #check to see if removing cases of 1 book reviews created cases where there is only 1 user 
over2usersOver2booksPart4 = over2usersOver2booksPart3.groupby('ISBN').filter(lambda x: len(x) >= 2) 
checkBooks = over2usersOver2booksPart4.groupby( 'UserID' ).ISBN.apply( lambda x: len( x ))  
over2usersOver2booksPart5 = over2usersOver2booksPart4.groupby('UserID').filter(lambda x: len(x) >= 2) 
checkBooks = over2usersOver2booksPart5.groupby( 'ISBN' ).ISBN.apply( lambda x: len( x ))  
over2usersOver2booksPart6 = over2usersOver2booksPart5.groupby('ISBN').filter(lambda x: len(x) >= 2) 
checkBooks = over2usersOver2booksPart6.groupby( 'UserID' ).ISBN.apply( lambda x: len( x ))  
over2usersOver2booksPart7 = over2usersOver2booksPart6.groupby('UserID').filter(lambda x: len(x) >= 2) 
checkBooks = over2usersOver2booksPart7.groupby( 'ISBN' ).ISBN.apply( lambda x: len( x ))  
over2usersOver2booksPart8 = over2usersOver2booksPart7.groupby('ISBN').filter(lambda x: len(x) >= 2) 
checkBooks = over2usersOver2booksPart8.groupby( 'UserID' ).ISBN.apply( lambda x: len( x ))  
checkBooks = over2usersOver2booksPart8.groupby( 'ISBN' ).ISBN.apply( lambda x: len( x ))  #Important to note total number of books is 40988




Finally, at least two occurances of each user and each book in the data. Lets check the number of data points we have left. 

In [12]:
over2usersOver2booksPart8.shape[0]

211322

The data will now be sorted by the number of occurances for each book. We will be mapping the ISBN with numbers (EmbedID) from 0 to the number of books , and these numbers will be used for looking of the vector for each book in the embedding and softmax matrices. For now, the data is ordered by book occurance (we will randomize the data later) so that books that occur more frequently in the data will have smaller number for the EmbedID. We are doing this because we will mostly be focusing on books that occur more frequently (and thus whose embeddings had more training) in the analysis, and arranging the EmbedID this way makes it easier. This probably doesn't make sence at the moment, but as you go through this notebook, the traning notebook, and the analysis notebook hopefully it'll be more clear. So if this doesn't quite make sense yet, wait until you have reviewed those notebooks and then come back to this section. 

In [13]:
over2usersOver2booksPart8['count'] = over2usersOver2booksPart8.groupby('ISBN')['ISBN'].transform(pd.Series.value_counts)
over2usersOver2booksPart8.head(5)

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  """Entry point for launching an IPython kernel.


UserID        ISBN  BookRating  count
16  276747  0060517794           9     26
19  276747  0671537458           9     14
20  276747  0679776818           8     14
59  276772  0553572369           7      7
61  276772  3499230933          10      3

In [14]:
sortedData = over2usersOver2booksPart8.sort_values('count', ascending=False)
sortedData.head(5)

UserID        ISBN  BookRating  count
549397   131686  0316666343           8    511
468822   112026  0316666343           8    511
990646   238131  0316666343           8    511
1117422  268110  0316666343           7    511
989554   238120  0316666343           7    511

In [15]:
sortedData2 = sortedData.drop('count', axis=1)
sortedData2.head(5)

UserID        ISBN  BookRating
549397   131686  0316666343           8
468822   112026  0316666343           8
990646   238131  0316666343           8
1117422  268110  0316666343           7
989554   238120  0316666343           7

In [0]:
sortedData2.to_csv('refinedBookCrossingsRatings4.csv') #To make it into a regular dataframe object again
                                                                                                      #There's probably a better way to convert the data into a dataframe object again
rr2 = pd.read_csv( 'refinedBookCrossingsRatings4.csv' )

Map each ISBN to a unique number called the EmbedID. This number will be used to look up a book's embedding from the embedding and softmax matrices. For example, a book with EmbedID of 7 will have it's embedding be the 7th row (or column; I forgot how the matrix is orientated) in the embedding and softmax matrix. 

In [17]:
mapping = {k: v for v, k in enumerate(rr2.ISBN.unique())}  #Give each book a unique ID for embedding matrix and softmax matrix lookup
rr2['EmbedID'] = rr2.ISBN.map(mapping)
rr2.head()

Unnamed: 0  UserID        ISBN  BookRating  EmbedID
0      549397  131686  0316666343           8        0
1      468822  112026  0316666343           8        0
2      990646  238131  0316666343           8        0
3     1117422  268110  0316666343           7        0
4      989554  238120  0316666343           7        0

Group the data by each User. This format is neccessary for the way I coded the training algorithm. This is for the algorithm to know which books for each data point to perform similiarity on. 

In [18]:
rr3= rr2.groupby(['UserID'], as_index=False, sort=True)

print(rr3.apply(lambda x: x.head(5)))

              Unnamed: 0  UserID        ISBN  BookRating  EmbedID
0     61670         9598      17  0891075275           6     1504
      120080        9594      17  0425099148           7     6515
1     4507          9607      26  0446310786          10       19
      14487         9608      26  0449005615           9      106
2     43342         9617      39  0671888587           7      732
      96544         9616      39  0553582909           8     4277
3     120281        9628      53  0380715899           9     7320
      160989        9626      53  0156047624          10    20221
4     65067         9632      56  0671623249           7     1698
      160974        9634      56  0679865691           9    17188
5     96204         9667      92  8445071408           7     4186
      120205        9669      92  8445071777          10     6591
      120206        9668      92  8445071769           8     6602
6     40196         9677      99  0446677450          10      611
      9299

This block will add two columns, one is a random number mapped for each user, and the other column is just a random number. These two columns will be used to randomize the order of the users, and the order of the books for each user. This is to prevent the training algorithm from fitting to the order of the data. I like to train on a few few versions of the data with this randomization.  

In [19]:
randomColumn1 = dict()
i=1
for n in random.sample(range(1, rr2['UserID'].max()+1), rr2['UserID'].max()):
  randomColumn1.update({i:n})
  i=i+1
  
rr2['SortIndex1'] = rr2['UserID'].map(randomColumn1)

rr2['SortIndex2'] = np.random.randint(1, 500, rr2.shape[0])
rr2.head()

Unnamed: 0  UserID        ISBN  BookRating  EmbedID  SortIndex1  SortIndex2
0      549397  131686  0316666343           8        0      141780         118
1      468822  112026  0316666343           8        0      206240         241
2      990646  238131  0316666343           8        0      143595         261
3     1117422  268110  0316666343           7        0       18551         196
4      989554  238120  0316666343           7        0       54964         375

In [20]:
r3 = rr2.sort_values(['SortIndex1', 'SortIndex2']) 

r3.head(5)

Unnamed: 0  UserID        ISBN  BookRating  EmbedID  SortIndex1  \
26024       136755   31134  089480829X           9      282           8   
44462       136741   31134  0060964049          10      774           8   
21733       136745   31134  0385498802           7      206           8   
205912      136748   31134  0446529540           7    33636           8   
57648       597537  144151  0140481389           6     1347          21   

        SortIndex2  
26024          199  
44462          290  
21733          317  
205912         499  
57648           17

Here I add a new column called 'Headernumber'. This column is used to keep track of data points that belong to a particular user. For the first instance of a particular user in the data, the headernumber is the number of data points for that user, and for the rest of the instances, the headernumber is '-1'. When the training algorithm is going through the data, the headernumber is used to match the right inputs with the right labels. How exactly the Headernumber is used will be explained more clearly in the training algorithm. 

In [21]:
r3['Headernumber'] = np.where(r3['UserID'].duplicated(), -1, 
                         r3.groupby('UserID')['UserID'].transform(len))

r3.head(5)

Unnamed: 0  UserID        ISBN  BookRating  EmbedID  SortIndex1  \
26024       136755   31134  089480829X           9      282           8   
44462       136741   31134  0060964049          10      774           8   
21733       136745   31134  0385498802           7      206           8   
205912      136748   31134  0446529540           7    33636           8   
57648       597537  144151  0140481389           6     1347          21   

        SortIndex2  Headernumber  
26024          199             4  
44462          290            -1  
21733          317            -1  
205912         499            -1  
57648           17             7

In [22]:
r3 = r3[['Unnamed: 0', 'UserID', 'EmbedID', 'BookRating', 'SortIndex1', 'SortIndex2',  'Headernumber',   'ISBN']]
r3.head(5)

Unnamed: 0  UserID  EmbedID  BookRating  SortIndex1  SortIndex2  \
26024       136755   31134      282           9           8         199   
44462       136741   31134      774          10           8         290   
21733       136745   31134      206           7           8         317   
205912      136748   31134    33636           7           8         499   
57648       597537  144151     1347           6          21          17   

        Headernumber        ISBN  
26024              4  089480829X  
44462             -1  0060964049  
21733             -1  0385498802  
205912            -1  0446529540  
57648              7  0140481389

Check how many books there are

In [23]:
r3.loc[r3['EmbedID'].idxmax()]

Unnamed: 0          716214
UserID              173486
EmbedID              40987
BookRating               9
SortIndex1          232601
SortIndex2              70
Headernumber            -1
ISBN            1573245232
Name: 211272, dtype: object

Since the training algorithm uses EmbedID, ISBN is dropped to reduce size of the data file. 

In [24]:
r4 = r3.drop(columns=['ISBN'])
r4.head(5)

Unnamed: 0  UserID  EmbedID  BookRating  SortIndex1  SortIndex2  \
26024       136755   31134      282           9           8         199   
44462       136741   31134      774          10           8         290   
21733       136745   31134      206           7           8         317   
205912      136748   31134    33636           7           8         499   
57648       597537  144151     1347           6          21          17   

        Headernumber  
26024              4  
44462             -1  
21733             -1  
205912            -1  
57648              7

Save the file

In [0]:
r4.to_csv('BookCrossingDataReadyForTraining6.csv', index=False)

Upload file to Google Drive 

In [0]:

uploadModel = drive.CreateFile()


uploadModel.SetContentFile("BookCrossingDataReadyForTraining6.csv") #name of file located in local disk 
uploadModel.Upload()

Now that we're done with the training data, lets create a data file which holds the EmbedID, ISBN, book title, and the author. First, lets download the BX-Books.csv file. 

In [27]:
dl_id = input("Enter Gdrive file ID for Book titles file: ") # 1kZBM8orAm9OpKLHWuVCp2YqFY-LxaYim

# DOWNLOAD ZIP
print ("Downloading  file")
myzip = drive.CreateFile({'id': dl_id})
myzip.GetContentFile('bookTitles.csv')

print( os.listdir() )

Enter Gdrive file ID for Book titles file: 1kZBM8orAm9OpKLHWuVCp2YqFY-LxaYim
['sample_data', '.config', 'adc.json', 'BookCrossingDataReadyForTraining6.csv', 'refinedBookCrossingsRatings4.csv', 'data.csv', 'bookTitles.csv', 'ratings.csv']


Open and convert data to a pandas dataframe

In [28]:
with open('bookTitles.csv', 'rb') as f:
  text = f.read()
bookfile = pd.read_csv('bookTitles.csv',  encoding = "ISO-8859-1", error_bad_lines=False, delimiter=';')
bookfile.head()

b'Skipping line 6452: expected 8 fields, saw 9\nSkipping line 43667: expected 8 fields, saw 10\nSkipping line 51751: expected 8 fields, saw 9\n'
b'Skipping line 92038: expected 8 fields, saw 9\nSkipping line 104319: expected 8 fields, saw 9\nSkipping line 121768: expected 8 fields, saw 9\n'
b'Skipping line 144058: expected 8 fields, saw 9\nSkipping line 150789: expected 8 fields, saw 9\nSkipping line 157128: expected 8 fields, saw 9\nSkipping line 180189: expected 8 fields, saw 9\nSkipping line 185738: expected 8 fields, saw 9\n'
b'Skipping line 209388: expected 8 fields, saw 9\nSkipping line 220626: expected 8 fields, saw 9\nSkipping line 227933: expected 8 fields, saw 11\nSkipping line 228957: expected 8 fields, saw 10\nSkipping line 245933: expected 8 fields, saw 9\nSkipping line 251296: expected 8 fields, saw 9\nSkipping line 259941: expected 8 fields, saw 9\nSkipping line 261529: expected 8 fields, saw 9\n'
/usr/local/lib/python3.6/dist-packages/IPython/core/interactiveshell.py:27

ISBN                                         Book-Title  \
0  0195153448                                Classical Mythology   
1  0002005018                                       Clara Callan   
2  0060973129                               Decision in Normandy   
3  0374157065  Flu: The Story of the Great Influenza Pandemic...   
4  0393045218                             The Mummies of Urumchi   

            Book-Author Year-Of-Publication                   Publisher  \
0    Mark P. O. Morford                2002     Oxford University Press   
1  Richard Bruce Wright                2001       HarperFlamingo Canada   
2          Carlo D'Este                1991             HarperPerennial   
3      Gina Bari Kolata                1999        Farrar Straus Giroux   
4       E. J. W. Barber                1999  W. W. Norton &amp; Company   

                                         Image-URL-S  \
0  http://images.amazon.com/images/P/0195153448.0...   
1  http://images.amazon.com/images/P/0002005018.0...   
2  http://images.amazon.com/images/P/0060973129.0...   
3  http://images.amazon.com/images/P/0374157065.0...   
4  http://images.amazon.com/images/P/0393045218.0...   

                                         Image-URL-M  \
0  http://images.amazon.com/images/P/0195153448.0...   
1  http://images.amazon.com/images/P/0002005018.0...   
2  http://images.amazon.com/images/P/0060973129.0...   
3  http://images.amazon.com/images/P/0374157065.0...   
4  http://images.amazon.com/images/P/0393045218.0...   

                                         Image-URL-L  
0  http://images.amazon.com/images/P/0195153448.0...  
1  http://images.amazon.com/images/P/0002005018.0...  
2  http://images.amazon.com/images/P/0060973129.0...  
3  http://images.amazon.com/images/P/0374157065.0...  
4  http://images.amazon.com/images/P/0393045218.0...

Create a dictionary for the ISBN and Title

In [29]:
bookDictionary = bookfile.set_index('ISBN').to_dict()['Book-Title']
bookDictionary['0393045218']

'The Mummies of Urumchi'

Create a dictionary for the ISBN and Title

In [30]:
authorDictionary = bookfile.set_index('ISBN').to_dict()['Book-Author']
authorDictionary['0393045218']

'E. J. W. Barber'

Use the dictionary to create columns for the r3 pandas dataframe for the book title and author

In [31]:
r3['Book_Title'] = r3['ISBN'].map(bookDictionary)
r3['Author'] = r3['ISBN'].map(authorDictionary)
r3.head(5)

Unnamed: 0  UserID  EmbedID  BookRating  SortIndex1  SortIndex2  \
26024       136755   31134      282           9           8         199   
44462       136741   31134      774          10           8         290   
21733       136745   31134      206           7           8         317   
205912      136748   31134    33636           7           8         499   
57648       597537  144151     1347           6          21          17   

        Headernumber        ISBN  \
26024              4  089480829X   
44462             -1  0060964049   
21733             -1  0385498802   
205912            -1  0446529540   
57648              7  0140481389   

                                               Book_Title            Author  
26024   What to Expect When You're Expecting (Revised ...  Arlene Eisenberg  
44462   Tales of the City (Tales of the City Series, V...  Armistead Maupin  
21733                                 Bee Season: A Novel     Myla Goldberg  
205912      Futureland: Nine Stories of an Imminent World     Walter Mosley  
57648   The Crucible: A Play in Four Acts (Penguin Plays)     Arthur Miller

Now we can create dictionary's to look up the book title and author from the EmbedID

In [32]:
bookDictionary2 = r3.set_index('EmbedID').to_dict()['Book_Title']
bookDictionary2[95]

'The Hours: A Novel'

In [33]:
authorDictionary2 = r3.set_index('EmbedID').to_dict()['Author']
authorDictionary2[135]

'Janet Evanovich'

Remove training data

In [0]:
r5 = r3.drop(columns=['Unnamed: 0', 'UserID', 'BookRating', 'SortIndex1', 'SortIndex2', 'Headernumber' ])

Remove duplicates


In [35]:
r5.drop_duplicates()
r5.head()

EmbedID        ISBN  \
26024       282  089480829X   
44462       774  0060964049   
21733       206  0385498802   
205912    33636  0446529540   
57648      1347  0140481389   

                                               Book_Title            Author  
26024   What to Expect When You're Expecting (Revised ...  Arlene Eisenberg  
44462   Tales of the City (Tales of the City Series, V...  Armistead Maupin  
21733                                 Bee Season: A Novel     Myla Goldberg  
205912      Futureland: Nine Stories of an Imminent World     Walter Mosley  
57648   The Crucible: A Play in Four Acts (Penguin Plays)     Arthur Miller

Save and upload file to Google drive

In [0]:
r5.to_csv('BookCrossingBookData3.csv', index=False)

uploadModel = drive.CreateFile()

uploadModel.SetContentFile("BookCrossingBookData3.csv") #name of file located in local disk 
uploadModel.Upload()

Now that we have refined the data, we can start training over it. 


Input Google drive file ID for the refined ratings file produced in BookCrossingsDataAnalysis.ipynb notebook


In [37]:
dl_id = input("Enter Gdrive file ID for Refined Ratings: ") #Book Crossing 1mtg_TdC4FBlbQh30Yt1-Rxcyu2Q38Axv


# DOWNLOAD ZIP
print ("Downloading  file")
myDownload = drive.CreateFile({'id': dl_id})
myDownload.GetContentFile('DlRefinedRatings.csv')
print( os.listdir() )

my_data = genfromtxt('DlRefinedRatings.csv', delimiter=',' ,  dtype=int, skip_header=1)

print(my_data[0:5])

Enter Gdrive file ID for Refined Ratings: 1mtg_TdC4FBlbQh30Yt1-Rxcyu2Q38Axv
['sample_data', '.config', 'adc.json', 'BookCrossingDataReadyForTraining6.csv', 'refinedBookCrossingsRatings4.csv', 'DlRefinedRatings.csv', 'data.csv', 'bookTitles.csv', 'BookCrossingBookData3.csv', 'ratings.csv']
[[1082427  259004     784       8      22      54      17]
 [1082450  259004   24422       7      22      91      -1]
 [1082415  259004    3085       7      22     183      -1]
 [1082363  259004   24458       6      22     250      -1]
 [1082357  259004    2465       6      22     251      -1]]


Input Google drive file ID for the book info file produced in BookCrossingsDataAnalysis.ipynb notebook

In [38]:
dl_id = input("Enter Gdrive file ID for Book info: ") #Book Crossing  1thtwqN1fhyiLeEnmj51ZhEaW5DgonYgC


# DOWNLOAD ZIP
print ("Downloading  file")
myDownload = drive.CreateFile({'id': dl_id})
myDownload.GetContentFile('BookInfo.csv')
print( os.listdir() )

Enter Gdrive file ID for Book info: 1thtwqN1fhyiLeEnmj51ZhEaW5DgonYgC
['sample_data', '.config', 'adc.json', 'BookInfo.csv', 'BookCrossingDataReadyForTraining6.csv', 'refinedBookCrossingsRatings4.csv', 'DlRefinedRatings.csv', 'data.csv', 'bookTitles.csv', 'BookCrossingBookData3.csv', 'ratings.csv']


Create dictionaries to look up Authors and Book Titles from the EmbedID

In [39]:
b = pd.read_csv( 'BookInfo.csv' )
b.head(30)
bookDictionary = b.set_index('EmbedID').to_dict()['Book_Title']
bookDictionary[7]
authorDictionary = b.set_index('EmbedID').to_dict()['Author']
authorDictionary[7]

'Dan Brown'

This code section produces a batch of input data and corresponding labels. 

In [0]:
data_index = 0
epoch_index = 0
recEpoch_indexA = 0 #Used to help keep store of the total number of epoches with the models

def generate_batch(batch_size, inputCount): 
  
    global data_index, epoch_index
    
    span = inputCount 
    batch = np.ndarray(shape=(batch_size, span), dtype=np.int32) 
    labels = np.ndarray(shape=(batch_size, 1), dtype=np.int32)
    
    
    userbracketDF = my_data[data_index: data_index+ my_data[data_index, 6], 2 ]
    headernumber = my_data[:,6]
    assert headernumber[data_index] != -1, 'data_index in incorrect spot. Most likely fix is to reset data_index to 0'
        
    n=0
    while n < batch_size:
      b=0
      while b < len(userbracketDF) and n < batch_size :
        #print('n is', n)
        if b== 0:
          potentialBatch=userbracketDF[b+1:len(userbracketDF)]
        else:
          firsthalf = userbracketDF[0:b]
          secondhalf = userbracketDF[b+1:len(userbracketDF)]
          potentialBatch = np.concatenate((firsthalf, secondhalf), axis=0)
        potentialBatchSet = set(potentialBatch)
        if inputCount > len(potentialBatchSet):
          print('potentialBatchSet is ', potentialBatchSet)
          print('data_index is ', data_index)
          raise Exception('Dataset is for a smaller Cbow Window, data needs to be checked') 
        batch[n] = random.sample(potentialBatchSet,  inputCount)
        labels[n,0]=userbracketDF[b]
        n=n+1
        b=b+1
      
      data_index = (data_index + headernumber[data_index] ) % len(headernumber)
      
      if data_index == 0:
        epoch_index = epoch_index + 1
        print('Completed %d Epochs' % epoch_index)
      
      #print('data_index is ', data_index)
      assert headernumber[data_index] != -1, 'data_index in incorrect spot'
      userbracketDF = my_data[data_index: data_index+ my_data[data_index, 6], 2 ]

    return batch, labels     
      
# here, goes = generate_batch(20, 1) # to do next, insert %len(headernumber)
# print('batch', here)
# print('labels', goes)

Define the graph

In [0]:
vocabulary_size =  40988 #number of books
batch_size = 128 #2^8

embedding_size = 200 # 2^8 Dimension of the embedding vector.
num_inputs =1
#skip_window = 1 # How many words to consider left and right.
#num_skips = 2 # How many times to reuse an input to generate a label.
                      
# We pick a random validation set to sample nearest neighbors. here we limit the
# validation samples to the words that have a low numeric ID, which by
# construction are also the most frequent. 
valid_size = 60 # Random set of words to evaluate similarity on.
valid_window = 5000 # Only pick dev samples in the head of the distribution.
#valid_examples = np.array(random.sample(range(valid_window), valid_size))
# Random set of words to evaluate similarity on.
num_sampled = 65 # Number of negative examples to sample.

graph = tf.Graph()

with graph.as_default(): #took out " , tf.device('/cpu:0')"
 
  valid_examples = np.array(random.sample(range(1, valid_window), valid_size)) #put inside graph to get new words each time
  #for same words each time keep outside graph
  
  # Input data.
  train_dataset = tf.placeholder(tf.int32, shape=[batch_size, num_inputs ])
  train_labels = tf.placeholder(tf.int32, shape=[batch_size, 1])
  valid_dataset = tf.constant(valid_examples, dtype=tf.int32)
  valid_datasetSM = tf.constant(valid_examples, dtype=tf.int32)

  epochCount = tf.get_variable( 'epochCount', initializer= 0) #to store epoch count to total # of epochs are known
  update_epoch = tf.assign(epochCount, epochCount + 1)
  # Variables.
  #embeddings = tf.Variable(
  #  tf.random_uniform([vocabulary_size, embedding_size], -1.0, 1.0))
  embeddings = tf.get_variable( 'embeddings', 
    initializer= tf.random_uniform([vocabulary_size, embedding_size], -1.0, 1.0))
  #softmax_weights = tf.Variable(
  #  tf.truncated_normal([vocabulary_size, embedding_size],
  #                       stddev=1.0 / math.sqrt(embedding_size)))
  softmax_weights = tf.get_variable( 'softmax_weights',
    initializer= tf.truncated_normal([vocabulary_size, embedding_size],
                         stddev=1.0 / math.sqrt(embedding_size)))
  
  softmax_biases = tf.get_variable('softmax_biases', 
    initializer= tf.zeros([vocabulary_size]),  trainable=False )
  #Made softmax biases untrainable because they do not seem to give significant
  #improvement. Also allows for a 2nd set of embeddings to analyze. 
  #https://stats.stackexchange.com/questions/249565/word2vec-neural-network-bias-units/250464
  #Both Richard Sorcher and Andrew Ng's NLP lectures do not contain a bias term
  #in their equations. 
  
  # Model.
  # Look up embeddings for inputs.
  embed = tf.nn.embedding_lookup(embeddings, train_dataset) #train data set is
  #the center word for skip-gram mode. So we're looking up the vector for that
  #center word. Gets the embeddings for every word in the batch
  # Compute the softmax loss, using a sample of the negative labels each time.
  embed_reshaped = tf.reshape( embed, [batch_size*num_inputs, embedding_size] )
  
  
  segments= np.arange(batch_size).repeat(num_inputs)
  #segments= np.arange(embedding_size).repeat(num_inputs)
  #should be batch size, not embedding size
  
  averaged_embeds = tf.segment_mean(embed_reshaped, segments, name=None)
  
  #def loss_function():
    #return tf.reduce_mean( tf.nn.sampled_softmax_loss(weights=softmax_weights, biases=softmax_biases, inputs=averaged_embeds,
                               #labels=train_labels, num_sampled=num_sampled, num_classes=vocabulary_size))
  
  loss = tf.reduce_mean(
    tf.nn.sampled_softmax_loss(weights=softmax_weights, biases=softmax_biases, inputs=averaged_embeds,
                               labels=train_labels, num_sampled=num_sampled, num_classes=vocabulary_size))
            #fun fact remove_accidental_hits: A bool. whether to remove "accidental hits" where 
            #a sampled class equals one of the target classes. Default is True.

  # Optimizer.
  # Note: The optimizer will optimize the softmax_weights AND the embeddings.
  # This is because the embeddings are defined as a variable quantity and the
  # optimizer's `minimize` method will by default modify all variable quantities 
  # that contribute to the tensor it is passed.
  # See docs on `tf.train.Optimizer.minimize()` for more details.
  optimizer = tf.train.AdagradOptimizer(0.03).minimize(loss) #Original learning rate was 1.0
  
  # Compute the similarity between minibatch examples and all embeddings.
  # We use the cosine distance:
  norm = tf.sqrt(tf.reduce_sum(tf.square(embeddings), 1, keepdims=True))
  normSM = tf.sqrt(tf.reduce_sum(tf.square(softmax_weights), 1, keepdims=True))
  
  normalized_embeddings = embeddings / norm
  normalized_embeddingsSM = softmax_weights / normSM
  
  valid_embeddings = tf.nn.embedding_lookup(
    normalized_embeddings, valid_dataset) #A bunch of normalized embeddings, randomly selected when valid_examples was initilized. 
  valid_embeddingsSM = tf.nn.embedding_lookup(
    normalized_embeddingsSM, valid_datasetSM)
  
  similarity = tf.matmul(valid_embeddings, tf.transpose(normalized_embeddings)) #multiplies each normalized embeds from valid_examples with all 
                                                                                                                        #other normalized embeds. Used to find most similiar embeds later
  similaritySM = tf.matmul(valid_embeddingsSM, tf.transpose(normalized_embeddingsSM)) 
  #important to note that to note that throughout all these matrix operations, indices of the original embedding and SM matrices are kept in tact
  #this is important for when we want to match an embedding with it's corresponding book, since the book dictionary uses the index as the key
                                                                                                                              
  saver = tf.train.Saver()

This zip folder is used to save the checkpoints and zip them into a zipfile so that they can be easily uploaded to Google Drive

In [0]:
def zipfolder(foldername, target_dir):            
    zipobj = zipfile.ZipFile(foldername + '.zip', 'w', zipfile.ZIP_DEFLATED)
    rootlen = len(target_dir) + 1
    for base, dirs, files in os.walk(target_dir):
        for file in files:
            fn = os.path.join(base, file)
            zipobj.write(fn, fn[rootlen:])

If you would like to continue from a previous Tensorflow checkpoint, select 'y' and put the Google file ID for the checkpoint

In [45]:
loadModel = input("Would you like to load a checkpoint? Type y or n: ") 

if loadModel == 'y':
  auth.authenticate_user()
  gauth = GoogleAuth()
  gauth.credentials = GoogleCredentials.get_application_default()
  drive = GoogleDrive(gauth)
  
  zip_id = input("Enter Gdrive file ID for tensorflow models: ") 

  if not os.path.exists('checkpointsBook2VecCbowWindow1Downloaded'):
      os.makedirs('checkpointsBook2VecCbowWindow1Downloaded')

  # DOWNLOAD ZIP
  print ("Downloading zip file")
  myzip = drive.CreateFile({'id': zip_id})
  myzip.GetContentFile('model.zip')

  # UNZIP ZIP
  print ("Uncompressing zip file")
  zip_ref = zipfile.ZipFile('model.zip', 'r')
  zip_ref.extractall('checkpointsBook2VecCbowWindow1Downloaded/')
  zip_ref.close()

  print( os.getcwd() )
  print( os.listdir('./checkpointsBook2VecCbowWindow1Downloaded') )
  
  #with tf.Session(graph=graph) as session:
    #saver = tf.train.import_meta_graph('./checkpointsBook2VecCbowWindow3Downloaded/bookVec.ckpt.meta')
    #saver.restore(session, './checkpointsBook2VecCbowWindow3Downloaded/bookVec.ckpt' )

Would you like to load a checkpoint? Type y or n: y
Enter Gdrive file ID for tensorflow models: 12DyYI6Q1YMajya3btReZw6-tUJJvGQuE
Uncompressing zip file
/content
['bookVec.ckpt.data-00000-of-00001', 'checkpoint', 'bookVec.ckpt.meta', 'bookVec.ckpt.index']


Run the Tensorflow graph in a session.

In [48]:
num_steps = 10000

if 'loadModel' not in locals() and 'loadModel' not in globals():
  loadModel = 'n'

uploadModel = drive.CreateFile() #used to upload checkpoints when graph is run

with tf.Session(graph=graph) as session:
  
  if loadModel == 'y':
    saver.restore(session, './checkpointsBook2VecCbowWindow1Downloaded/bookVec.ckpt' )
  else:  
    tf.global_variables_initializer().run() #Don't initalize variables after a checkpoint has been restored
  
  print('Initialized')
  average_loss = 0
  saveIteration = 1
  for step in range(1, num_steps):
    
    batch_data, batch_labels = generate_batch(
      batch_size, num_inputs)
    #print(batch_data)
    feed_dict = {train_dataset : batch_data, train_labels : batch_labels}
    #graph_batch = session.run([train_dataset], feed_dict=feed_dict) 
    #print(graph_batch)
    _, l = session.run([optimizer, loss], feed_dict=feed_dict) 

    average_loss += l
    if step % 1000 == 0:
      if step > 0:
        average_loss = average_loss / 1000
      # The average loss is an estimate of the loss over the last 2000 batches.
      print('Average loss at step %d: %f' % (step, average_loss))
      average_loss = 0
    # note that this is expensive (~20% slowdown if computed every 500 steps)
    
    if step % 5000 == 0:
      sim = similarity.eval()
      for i in range(valid_size):
        valid_word = bookDictionary[valid_examples[i]]
        top_k = 8 # number of nearest neighbors
        nearest = (-sim[i, :]).argsort()[1:top_k+1] #Returns index of most similiar values. Starts from 1 because index 0 will just be the same book
        log = 'Nearest to %s : | ' % valid_word
        for k in range(top_k):
          close_word = bookDictionary[nearest[k]]
          log = '%s %s | ' % (log, close_word) #Prints out most similiar books, in descending order from most to least similiar
        print(log)
        if gauth.credentials is None:
        # Authenticate if they're not there
          gauth.LocalWebserverAuth()
        elif gauth.access_token_expired:
          # Refresh them if expired
          print( "Google Drive Token Expired, Refreshing")
          gauth.Refresh()
        else:
          # Initialize the saved creds
          gauth.Authorize()
      
    if step % 150000 == 0:
      recEpoch_indexA =  epoch_index - recEpoch_indexA #how much did the epoch_index since it was last checked
      #epochCount = tf.add(  epochCount, recEpoch_indexA, name=None )
      for nE in range(0, recEpoch_indexA ):
        session.run(update_epoch) #session run calls tend to be huge bottlenecks, keep in mind while determining the frequency
      recEpoch_indexA = epoch_index
      print('recEpoch_indexA is', recEpoch_indexA)
      print( 'epochCount.eval() is ', epochCount.eval() )
      print('epoch_index is ' , epoch_index)
      
      save_path = saver.save(session, "B2VBookCrossingsckpt/bookVec.ckpt") #Save checkpoint
      
      auth.authenticate_user()
      gauth = GoogleAuth() #Gdrive authenticion code placed here since it expires after some time
      gauth.credentials = GoogleCredentials.get_application_default()
      drive = GoogleDrive(gauth) 
      uploadModel = drive.CreateFile() #Need to also create drive object with updated authenticion
      
      chptName = 'B2VBookCrossingsckpt'+str(saveIteration)
      zipfolder(chptName, 'B2VBookCrossingsckpt') #2nd input is the folder name of the save path
      uploadModel.SetContentFile(chptName+".zip")
      uploadModel.Upload()
      
      print("Checkpoint uploaded to Google Drive")
      saveIteration += 1
      os.remove(chptName+".zip") #Remove checkpoint zip file after upload

                
  #extract the embeddings
  final_embeddings = normalized_embeddings.eval() #extract the embeddings
  final_embeddingsSM = normalized_embeddingsSM.eval()

INFO:tensorflow:Restoring parameters from ./checkpointsBook2VecCbowWindow1Downloaded/bookVec.ckpt
Initialized
Completed 29 Epochs
Average loss at step 1000: 1.633372
Completed 30 Epochs
Average loss at step 2000: 1.649139
Average loss at step 3000: 1.633422
Completed 31 Epochs
Average loss at step 4000: 1.622264
Completed 32 Epochs
Average loss at step 5000: 1.640784
Nearest to Patty Jane's House of Curl : |  Green Journey |  Farm Fatale: A Comedy of Country Manors |  Daisy Fay and the Miracle Man |  Patty Jane's House of Curl (Ballantine Reader's Circle) |  Miss Nelson Is Missing! |  Esther's Gift: A Mitford Christmas Story (Christmas in Mitford Gift) |  The Chili Queen: A Novel |  The Crossroad | 
Nearest to On a Wicked Dawn (Cynster Novels) : |  Forbidden Knowledge: From Prometheus to Pornography |  Pillow Talk (Avon Light Contemporary Romances) |  Orchid Blues (Holly Barker Novels (Hardcover)) |  Reckless Love (Big Book) (Harlequin Historical, No 199) |  The Summerhouse |  Irresist

The trained embeddings are analyzed in much more detail in the BookCrossingsAnalyzeEmbeddings.ipynb file. In this session only 25 epoches were performed, but the embeddings analyzed in the next section were trained on over 100 epoches. 

Now that the embeddings are trained, we can analyze them. 

In [49]:
import re
from collections import Counter
import time

%matplotlib inline
from __future__ import print_function
import collections
import math
from matplotlib import pyplot
from six.moves import range
from six.moves.urllib.request import urlretrieve
from sklearn.manifold import TSNE

from urllib.request import urlretrieve
from os.path import isfile, isdir

!pip install adjustText #Helps prevent overlapping annotations on the scatter plots

from adjustText import adjust_text
!pip install pillow 

  Running setup.py bdist_wheel for adjustText ... - done
  Stored in directory: /root/.cache/pip/wheels/41/95/74/7d347e136d672f8bc28e937032bc92baf4f80856763a7e7b72
Successfully built adjustText


Input Google Drive file for the Tensorflow Checkpoint


In [50]:
zip_id = input("Enter Gdrive file ID for tensorflow models: ") # you can use this file ID 1dPjSl7Q6ULsxVUMbRogfY1E-cA5cC1He

if not os.path.exists('MODEL'):
    os.makedirs('MODEL')

# DOWNLOAD ZIP
print ("Downloading zip file")
myzip = drive.CreateFile({'id': zip_id})
myzip.GetContentFile('model.zip')

# UNZIP ZIP
print ("Uncompressing zip file")
zip_ref = zipfile.ZipFile('model.zip', 'r')
zip_ref.extractall('MODEL/')
zip_ref.close()

print( os.getcwd() )
print( os.listdir('./MODEL') )

Enter Gdrive file ID for tensorflow models: 1dPjSl7Q6ULsxVUMbRogfY1E-cA5cC1He
Uncompressing zip file
/content
['bookVec.ckpt.data-00000-of-00001', 'checkpoint', 'bookVec.ckpt.meta', 'bookVec.ckpt.index']


Input Google drive file ID for the book info file produced in BookCrossingsDataAnalysis.ipynb notebook, create dictionaries for the book title and author

In [51]:
dl_id = input("Enter Gdrive file ID for books: ") # you can use this file ID 1thtwqN1fhyiLeEnmj51ZhEaW5DgonYgC

# DOWNLOAD ZIP
print ("Downloading  file")
myzip = drive.CreateFile({'id': dl_id})
myzip.GetContentFile('books.csv')

b = pd.read_csv( 'books.csv' )
b.head(30)
bookDictionary = b.set_index('EmbedID').to_dict()['Book_Title']
bookDictionary[5]
AuthorDictionary = b.set_index('EmbedID').to_dict()['Author']

Enter Gdrive file ID for books: 1thtwqN1fhyiLeEnmj51ZhEaW5DgonYgC


Extract the book embeddings for the input embedding matrix and softmax matrix.

In [52]:
with tf.Session() as sess:
  saver = tf.train.import_meta_graph('./MODEL/bookVec.ckpt.meta')
  saver.restore(sess, './MODEL/bookVec.ckpt' )

  embeddings = tf.get_default_graph().get_tensor_by_name('embeddings:0') #Getting regular embeddings
  softmax_weights = tf.get_default_graph().get_tensor_by_name('softmax_weights:0') #Get softmax embeddings
  
  normSM = tf.sqrt(tf.reduce_sum(tf.square(softmax_weights), 1, keepdims=True))
  normalized_embeddingsSM = softmax_weights / normSM
  
  norm = tf.sqrt(tf.reduce_sum(tf.square(embeddings), 1, keepdims=True))
  normalized_embeddings = embeddings / norm
  
  final_embeddings = normalized_embeddings.eval()
  final_embeddingsSM = normalized_embeddingsSM.eval()

INFO:tensorflow:Restoring parameters from ./MODEL/bookVec.ckpt


The following code blocks can look up the EmbedId from either the Author or Book Title. You don't have to use the exact author or title, you can just input a word and the code block will return all results which contain that word. 

In [53]:
#Use this code to get the book_id for any book using the authur name, using their full name, first name, or last name.  
#The search is case sensitive,  capitalize the first letter of any name. 

authorPhrase = 'Isaacson'
lines = []
for i in AuthorDictionary:
  if type(AuthorDictionary[i]) is str:
    if authorPhrase in AuthorDictionary[i] :
        lines.append(i)
for j in lines:
  print( bookDictionary[j], AuthorDictionary[j], ' | EmbedID: ', j  )

Benjamin Franklin : An American Life Walter Isaacson  | EmbedID:  34204
Benjamin Franklin : An American Life Walter Isaacson  | EmbedID:  37307


In [54]:
#Use this code to get the book_id for any book using the title, or a word in the title. 
#The search is case sensitive. All words in a title tend to be capitalized. 

searchPhrase = 'Wardrobe'
lines = []
for i in bookDictionary:
  if type(bookDictionary[i]) is str:
    if searchPhrase in bookDictionary[i] :
        lines.append(i)
for j in lines:
  print( bookDictionary[j], AuthorDictionary[j], ' | EmbedID: ', j  )

The Lion, the Witch and the Wardrobe (rpkg) (Narnia) C. S. Lewis  | EmbedID:  2426
Lion, the Witch and the Wardrobe C.S. Lewis  | EmbedID:  1051
The Lion, the Witch and the Wardrobe C. S. Lewis  | EmbedID:  25775
The Lion, the Witch, and the Wardrobe (The Chronicles of Narnia, Book 2) C. S. Lewis  | EmbedID:  514
The Lion, the Witch and the Wardrobe (The Chronicles of Narnia) C. S. Lewis  | EmbedID:  7405
The Lion, the Witch and the Wardrobe (Full-Color Collector's Edition) C. S. Lewis  | EmbedID:  1895
Chic Simple Dress Smart for Women: Wardrobes that Win in the Workplace Kim Johnson Gross  | EmbedID:  29894
Brenda's Wardrobe Companion:  A Guide to Getting Dressed From the Inside Out Brenda Kinsel  | EmbedID:  30883
The Chronicles of Narnia: The Magician's Nephew/The Lion, the Witch and the Wardrobe/The Horse and His Boy/Prince Caspian/Voyage of the Dawn Treader/The Silver Chair/The Last Battle C. S. Lewis  | EmbedID:  22117
The Lion, the Witch, and the Wardrobe C.S. Lewis  | EmbedID:

The following code cells are show which books are most similiar to a particular book. The book_id is used to get its corresponding embedding, and then a dot product a calculated between that embedding and all other embeddings to find the most similiar embeddings. The most similiar embeddings have their corresponding book title and author names printed out, starting with the most similiar. 

In [55]:
#Harry Potter and the Prisoner of Azkaban (Book 3) J. K. Rowling  | EmbedID:  44

JaneA = np.take(final_embeddings, 44, axis=0)   
similarityJaneA = np.matmul(JaneA, np.transpose(final_embeddings))

nearestJaneA = (-similarityJaneA).argsort()[0:15]

print('Most similiar to ', bookDictionary[nearestJaneA[0]], 'by',  AuthorDictionary[nearestJaneA[0]], '\n')

for k in range(0, 15):
  print(bookDictionary[nearestJaneA[k]], AuthorDictionary[nearestJaneA[k]])

Most similiar to  Harry Potter and the Prisoner of Azkaban (Book 3) by J. K. Rowling 

Harry Potter and the Prisoner of Azkaban (Book 3) J. K. Rowling
Harry Potter and the Chamber of Secrets (Book 2) J. K. Rowling
Harry Potter and the Goblet of Fire (Book 4) J. K. Rowling
Harry Potter and the Sorcerer's Stone (Book 1) J. K. Rowling
Harry Potter and the Order of the Phoenix (Book 5) J. K. Rowling
nan nan
1999 Writer's Market (Annual) Kirsten Holm
The Essential Calvin and Hobbes Bill Watterson
The Hanged Man T. J. MacGregor
Porno Irvine Welsh
The Lays of Beleriand (The History of Middle-Earth - Volume 3) J. R. R. Tolkien
nan nan
Caesar Colleen McCullough
So Long, and Thanks for All the Fish DOUGLAS ADAMS
The Book Lover's Kit Deborah Grandinetti


In [56]:
#James and the Giant Peach Roald Dahl  | EmbedID:  1492

JaneA = np.take(final_embeddings, 1492, axis=0) 
similarityJaneA = np.matmul(JaneA, np.transpose(final_embeddings))

nearestJaneA = (-similarityJaneA).argsort()[0:15]

for k in range(0, 15):
  print(bookDictionary[nearestJaneA[k]], AuthorDictionary[nearestJaneA[k]])

James and the Giant Peach Roald Dahl
Good things: The best of Martha Stewart living Martha Stewart
The Secret of Platform 13 Eva Ibbotson
The Bridegroom: Stories (Vintage International (Paperback)) Ha Jin
Mara and Dann Doris Lessing
Sunset Limited James Lee Burke
Men, Women and Relationships John Gray
Dreams in the Golden Country: The Diary of Zipporah Feldman, a Jewish Immigrant Girl, New York City, 1903 (Dear America) Kathryn Lasky
River of Blue Fire (Otherland, Volume 2) Tad Williams
PRINCESS Jude Deveraux
The Pilot's Wife Anita Shreve
Christianity, Social Tolerance, and Homosexuality: Gay People in Western Europe from the Beginning of the Christian Era to the Fourteenth Century John Boswell
October Sky: A Memoir Homer Hickam
Shoulders: A Novel Georgia Cotrell
Reservation Road John Burnham Schwartz


In [57]:
#Pride and Prejudice Jane Austen  | EmbedID:  610

JaneA = np.take(final_embeddings, 610, axis=0) 
similarityJaneA = np.matmul(JaneA, np.transpose(final_embeddings))

nearestJaneA = (-similarityJaneA).argsort()[0:15]

for k in range(0, 15):
  print(bookDictionary[nearestJaneA[k]], AuthorDictionary[nearestJaneA[k]])

Pride and Prejudice Jane Austen
The Curious Sofa: A Pornographic Work by Ogdred Weary Edward Gorey
Emma JANE AUSTEN
So Long, and Thanks for All the Fish DOUGLAS ADAMS
Mystery Peter Straub
Final Fantasy VIII Official Strategy Guide David Cassady
A Tan and Sandy Silence (Travis McGee Mysteries) John D. MacDonald
The 776 Stupidest Things Ever Said Ross Petras
The Complete Idiot's Guide to Decoding Your Genes Linda Tagliaferro
Sense and Sensibility Jane Austen
The Empty House Rosamunde Pilcher
Mates, Dates, and Sole Survivors (Mates, Dates) Cathy Hopkins
Election: A Novel Tom Perrotta
Three Complete Novels: Daring to Dream/Holding the Dream/Finding the Dream (Dream) Nora Roberts
The House of Sleep (Vintage Contemporaries (Paperback)) Jonathan Coe


In [58]:
#The Lion, the Witch, and the Wardrobe (The Chronicles of Narnia, Book 2) C. S. Lewis  | EmbedID:  514

JaneA = np.take(final_embeddings, 514, axis=0) 
similarityJaneA = np.matmul(JaneA, np.transpose(final_embeddings))

nearestJaneA = (-similarityJaneA).argsort()[0:15]

for k in range(0, 15):
  print(bookDictionary[nearestJaneA[k]], AuthorDictionary[nearestJaneA[k]])

The Lion, the Witch, and the Wardrobe (The Chronicles of Narnia, Book 2) C. S. Lewis
The Horse and His Boy C. S. Lewis
The Magician's Nephew (rack) (Narnia) C. S. Lewis
The Last Battle C. S. Lewis
Prince Caspian (rack) : The Return to Narnia (Narnia) C. S. Lewis
Pug Shots Jim Dratfield
The Voyage of the Dawn Treader (rack) (Narnia) C. S. Lewis
Rachel's Tears: The Spiritual Journey of Columbine Martyr Rachel Scott Darrell Scott
The Broken Cord: A Family's Ongoing Struggle With Fetal Alcohol Syndrome Michael Dorris
Interview with the Vampire : Anniversary edition ANNE RICE
The Kill Fee (Van Womer, Laura) Laura Van Wormer
Trainspotting John Hodge
Night Shift Stephen King
nan nan
Haunted Schools: True Ghost Stories (True Ghost Stories) Allan Zullo


In [59]:
#Benjamin Franklin : An American Life Walter Isaacson  | EmbedID:  34204

JaneA = np.take(final_embeddings, 34204, axis=0) 
similarityJaneA = np.matmul(JaneA, np.transpose(final_embeddings))

nearestJaneA = (-similarityJaneA).argsort()[0:15]

for k in range(0, 15):
  print(bookDictionary[nearestJaneA[k]], AuthorDictionary[nearestJaneA[k]])

Benjamin Franklin : An American Life Walter Isaacson
Eating Well For Optimum Health: The Essential Guide to Bringing Health and Pleasure Back to Eating Andrew Weil
Perdido Street Station China Mieville
Amazing Gracie: A Dog's Tale Dan Dye
San Andreas Alistair MacLean
High Five (A Stephanie Plum Novel) Janet Evanovich
Ten Big Ones: A Stephanie Plum Novel Janet Evanovich
Barchester Towers (Penguin Classics) Anthony Trollope
Home Song Lavyrle Spencer
Night Of The Full Moon (Stepping Stone,  paper) GLORIA WHELAN
Thale's Folly Dorothy Gilman
nan nan
Last Orders Graham Swift
GHOST STY Peter Straub
Our Story: 77 Hours That Tested Our Friendship and Our Faith The Quecreek Miners


Of course, there are 40,886 other books to evaluate, but evaluating all those books would be very time-consuming. A way to evaluate a large number of books  is TSNE, which maps the embeddings into a 2D or 3D space where embeddings that are most similar to each other are plotted close to each other (more elegantly explained here https://www.youtube.com/watch?v=p3wFE85dAyY ). 

I performed a TSNE of the most occurring 2770 books for both the input embeddings.  the map did not really make much sense to me. (you probably have to download these, open them up, and zoom in to read the maps)

In [0]:
num_points2 = 2770
books = [bookDictionary[i] for i in range(0, num_points2+1)]

tsne = TSNE(perplexity=50, n_components=2, init='pca', n_iter=5000, method='exact')
two_d_embeddings = tsne.fit_transform(final_embeddings[0:num_points2+1, :])

auth.authenticate_user()
gauth = GoogleAuth()
gauth.credentials = GoogleCredentials.get_application_default()
drive = GoogleDrive(gauth)
    
np.save('BookCrossings.npy', two_d_embeddings)  #TNSE may take a lot of time, so may be helpful to save the variable
uploadModel = drive.CreateFile()
uploadModel.SetContentFile('BookCrossings.npy')
uploadModel.Upload()

two_d_embeddingsSM = tsne.fit_transform(final_embeddingsSM[0:num_points2+1, :])

auth.authenticate_user()
gauth = GoogleAuth()
gauth.credentials = GoogleCredentials.get_application_default()
drive = GoogleDrive(gauth)
    
np.save('BookCrossingsSM.npy', two_d_embeddingsSM)  #TNSE may take a lot of time, so may be helpful to save the variable
uploadModel = drive.CreateFile()
uploadModel.SetContentFile('BookCrossingsSM.npy')
uploadModel.Upload()

Upload saved TSNE variable from Google drive using the Google Drive file ID of the numpy variable. 

In [61]:
loadModel = input("Would you like to load a TSNE varible? Type y or n ")  #  1ZgCG3KtUTVe8pUzlDiTHYOD5jXfbBAlQ

if loadModel == 'y':
  num_points2 = 2770
  auth.authenticate_user()
  gauth = GoogleAuth()
  gauth.credentials = GoogleCredentials.get_application_default()
  drive = GoogleDrive(gauth)
  
  tsne_id = input("Enter Gdrive file ID for numpy variable: ") # 

  getTsne = drive.CreateFile({'id': tsne_id})
  getTsne.GetContentFile('tnsedl.npy')

  two_d_embeddingsLoaded2 = np.load('tnsedl.npy')

Would you like to load a TSNE varible? Type y or n y
Enter Gdrive file ID for numpy variable: 1ZgCG3KtUTVe8pUzlDiTHYOD5jXfbBAlQ


Plot the TSNE

In [62]:
auth.authenticate_user()
gauth = GoogleAuth()
gauth.credentials = GoogleCredentials.get_application_default()
drive = GoogleDrive(gauth)
uploadModel = drive.CreateFile()

# from adjustText import adjust_text
# import numpy as np
# import pandas as pd

texts = []

def plot(embeddings, labels):
  assert embeddings.shape[0] >= len(labels), 'More labels than embeddings'
  pyplot.figure(figsize=(130, 130))  # in inches best sofar 275
  print('step4')
  for i, label in enumerate(labels):
    x, y = embeddings[i,:]
    pyplot.scatter(x, y)
    #texts.append(pyplot.text(x[i], y[i], label))
    #pyplot.annotate(label, xy=(x, y), xytext=(5, 2), textcoords='offset points', 3
                   #ha='right', va='bottom')
    #pyplot.text(x, y, label) 
    texts.append(pyplot.text(x, y, label))
    
  print('step5')  
  auth.authenticate_user()
  gauth = GoogleAuth()
  gauth.credentials = GoogleCredentials.get_application_default()
  drive = GoogleDrive(gauth)
  
  adjust_text(texts , arrowprops=dict(arrowstyle='->', color='#8f1402' , linewidth=0.7 ),  save_steps = False, save_prefix = 'Finalm', \
              autoalign = False ) #,  force_text=(0.2, 0.5 ), force_points=(0.4, 1.0), force_objects=(0.2, 0.5) got to 148 . try 110 next time
  
  print('step6')
  auth.authenticate_user()
  gauth = GoogleAuth()
  gauth.credentials = GoogleCredentials.get_application_default()
  drive = GoogleDrive(gauth)
  
  pyplot.savefig('Final2SM.jpg', bbox_inches='tight')
  uploadModel = drive.CreateFile()
  uploadModel.SetContentFile('Final2SM.jpg')
  uploadModel.Upload()
  
#   pyplot.savefig('Final2.png', bbox_inches='tight')
#   uploadModel = drive.CreateFile()
#   uploadModel.SetContentFile('Final2.png')
#   uploadModel.Upload()
  print('step7')
  #pyplot.show()


books = [bookDictionary[i] for i in range(1, num_points2+1)]
print('step3')
plot(two_d_embeddingsLoaded2, books)

step3
step4
step5
step6
step7
